# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model
(Recurrent PPO) [default: 25 EVs per week simulation]

Installing required packages and dependencies

In [ ]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [ ]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/
%ls

In [ ]:
import yaml
import numpy as np
from gym import Env
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import RecurrentPPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
#!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.15
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.20.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.15', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.20.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.15\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.20.0\n')


In [ ]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [ ]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
#case = 'wohnblock_household_simulation_adaptive_10.yaml' #(10 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_15.yaml' #(15 EVs arrivals per week with 50% average battery)
#case = 'wohnblock_household_simulation_adaptive_25.yaml' #(25 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_35.yaml' #(35 EVs arrivals per week with 50% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7fd3166d14d0>Mean parking time: 23.99
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 20
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 20, 'EVs_n_max': 1044, 'mean_park': 23.99, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_ener

In [ ]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
#env.plot_VPP_input_data()

Charging event: 1, Arrival time: 2022-01-01 16:00:00, Parking_time: 24, Leaving_time: 2022-01-02 16:00:00, SOC: 0.49496227773194484, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 1043, Arrival time: 2022-12-31 20:45:00, Parking_time: 23.578428446120405, Leaving_time: 2023-01-01 20:19:42.342406, SOC: 0.5554751860807596, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -21214.64 , Grid_used_en(grid-import)=4947.18kWh , autarky-rate=83.0 , RE-to-vehicle_unused_en(grid-export)=-26161.81kWh , self-consump.rate=47.9 , Total_selling_cost=€  -489.75 , Grid_cost=€  233.11
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  21579.38 , Grid_used_en=kWh  38799.27 , RE-to-vehicle_unused_en=kWh  17219.89 , Total_selling_cost=€  879.97 , Grid_cost=€  1373.61 , Charging_events=  1043 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  75.08


In [ ]:
env.plot_ELVIS_data()

In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
#env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  21422.53 , Grid_used_en(grid-import)=38497.95kWh , Total_demand=71682.91kWh , autarky-rate=46.3 , RE-to-vehicle_unused_en(grid-export)=17075.42kWh , Total_supply=50260.39kWh , self-consump.rate=66.0 , Grid_cost=€  1359.92 , Total_selling_cost=€  880.71 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [ ]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_autarky()

In [ ]:
#env.plot_Elvis_results()

In [ ]:
#env.plot_VPP_results()

In [ ]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_actions_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
## Wandb login to load models
#In Colab, uncomment below:
# %env "WANDB_DISABLE_CODE" True
# %env "WANDB_NOTEBOOK_NAME" "VPP_simulator.ipynb"
# os.environ['WANDB_NOTEBOOK_NAME'] = 'VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

In [ ]:
#Loading training model, from local directory or from wandb previous trainings
RecurrentPPO_path = "trained_models/RecurrentPPO_models/model_RecurrentPPO_"

#model_id = "s37o8q0n"
model_id = "333ckz0i"
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


## Testing dataset VPP Simulation using the loaded trained model

In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

#Save the VPP table
VPP_table = env.save_VPP_table(save_path='data/environment_optimized_output/VPP_table.csv')

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  21582.02 , Grid_used_en(grid-import)=39118.43kWh , Total_demand=71824.51kWh , autarky-rate=45.5 , RE-to-vehicle_unused_en(grid-export)=17536.4kWh , Total_supply=50242.49kWh , self-consump.rate=65.1 , Grid_cost=€  1373.67 , Total_selling_cost=€  878.24 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -3972.47 , Grid_used_en(grid-import)=2192.24kWh , Total_demand=59021.32kWh , autarky-rate=96.3 , RE-to-vehicle_unused_en(grid-export)=6164.71kWh , Total_supply=62993.79kWh , self-consump.rate=90.2 , Total_selling_cost=€  -75.53 , Grid_cost=€  79.85 
 EV_INFO: Av.EV_energy_leaving=kWh  66.63 , Std.EV_energy_leaving=kWh  23.54 , EV_departures =  1044 , EV_queue_left =  0
SCORE:  Cumulative_reward= 401576.78 - Step_rewars (load_t= 364188.8, EVs_ene

In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00  55.296196  55.189003   0.000000  51.400265   
2022-01-01 00:15:00  55.546196  54.138138   0.000000  51.650265   
2022-01-01 00:30:00  55.796196  53.065563   0.000000  51.900265   
2022-01-01 00:45:00  56.046196  52.256367   0.000000  52.150265   
2022-01-01 01:00:00  56.296196  51.325989   0.000000  52.400265   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  75.652809  37.515656  63.077850  99.989998   
2022-06-06 05:00:00  76.715111  37.265656  64.140152  99.989998   
2022-06-06 05:15:00  77.765366  37.015656  65.190407  35.393276   
2022-06-06 05:30:00  77.765366  37.015656  66.664345  36.867210   
2022-06-06 05:45:00  77.765366  37.015656  68.087807  38.290672   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [1, 2, 2, 1]   
2022-01-01 00:15:00     [3129, 3128, 0, 3127]  [1, 2, 2, 1]   
2022-01-01 00:30:00     [3129, 3128, 0, 3127]  [1, 2, 2, 1]   
2022-01-01 00:45:00     [3129, 3128, 0, 3127]  [1, 2, 2, 1]   
2022-01-01 01:00:00     [3129, 3128, 0, 3127]  [1, 2, 2, 1]   
...                                       ...           ...   
2022-06-06 04:45:00  [3595, 3594, 3593, 3592]  [1, 2, 1, 1]   
2022-06-06 05:00:00  [3595, 3594, 3593, 3592]  [1, 2, 1, 1]   
2022-06-06 05:15:00  [3595, 3594, 3593, 3596]  [0, 0, 1, 1]   
2022-06-06 05:30:00  [3595, 3594, 3593, 3596]  [0, 0, 1, 1]   
2022-06-06 05:45:00  [3595, 3594, 3593, 3596]  [0, 0, 1, 1]   

                                       mask_truth  ev_charged_pwr  \
time                                                                
2022-01-01 00:00:00  [False, False, False, False]        0.000000   
2022-01-01 00:15:00   [False, True, False, False]        2.000000   
2022-01-01 00:30:00   [False, True, False, False]        2.000000   
2022-01-01 00:45:00   [False, True, False, False]        2.000000   
2022-01-01 01:00:00   [False, True, False, False]        2.000000   
...                                           ...             ...   
2022-06-06 04:45:00    [True, False, True, False]        8.547738   
2022-06-06 05:00:00    [True, False, True, False]        8.498414   
2022-06-06 05:15:00      [True, True, True, True]        8.402038   
2022-06-06 05:30:00      [True, True, True, True]       11.791476   
2022-06-06 05:45:00     [True, False, True, True]       11.387697   

                     ev_discharged_pwr          load  load_reward  EV_reward  \
time                                                                           
2022-01-01 00:00:00           0.000000  1.804736e+00    15.000000        0.0   
2022-01-01 00:15:00          -4.203454  0.000000e+00    15.000000        0.0   
2022-01-01 00:30:00          -4.290305  0.000000e+00    15.000000        0.0   
2022-01-01 00:45:00          -3.236785 -2.220446e-16    15.000000        0.0   
2022-01-01 01:00:00          -3.721513  0.000000e+00    15.000000        0.0   
...                                ...           ...          ...        ...   
2022-06-06 04:45:00          -1.000000 -2.960303e+00    -5.226540        0.0   
2022-06-06 05:00:00          -1.000000 -4.249194e+00    -5.182733       50.1   
2022-06-06 05:15:00          -1.000000 -4.201006e+00    15.000000        0.0   
2022-06-06 05:30:00           0.000000  0.000000e+00    15.000000        0.0   
2022-06-06 05:45:00           0.000000  0.000000e+00    15.000000        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  15.000000  
2022-01-01 00:15:00  15.000000  
2022-01-01 00:30:00  15.000000  
2022-01-01 00:45:00  15.000000  
2022-01-01 01:00:00  15.000000  
...                        ...  
2022-06-06 04:45:00  -5.226540  
2022-06-06 05:00:00  44.917267  
2022-06-06 05:15:00  15.000000  
2022-06-06 05:30:00  15.000000  
20

In [ ]:
env.plot_VPP_autarky()

In [ ]:
#env.plot_Elvis_results()

In [ ]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Validating dataset VPP Simulation using the loaded trained model

In [ ]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 4173, Arrival time: 2022-01-02 14:00:00, Parking_time: 23.954801318274797, Leaving_time: 2022-01-03 13:57:17.284746, SOC: 0.537449473649571, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 5215, Arrival time: 2022-12-31 18:00:00, Parking_time: 23.19308059908044, Leaving_time: 2023-01-01 17:11:35.090157, SOC: 0.49420878295357556, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , Grid_used_en(grid-import)=2136.67kWh , autarky-rate=89.6 , RE-to-vehicle_unused_en(grid-export)=-32222.06kWh , self-consump.rate=36.4 , Total_selling_cost=€  -1187.15 , Grid_cost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  12729.85 , Grid_used_en=kWh  34224.73 , RE-to-vehicle_unused_en=kWh  21494.88 , Total_selling_cost=€  643.76 , Grid_cost=€  1511.43 , Charging_events=  1043 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  80.89


In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
#env.plot_VPP_input_data()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  12470.13 , Grid_used_en(grid-import)=34102.44kWh , Total_demand=63109.83kWh , autarky-rate=46.0 , RE-to-vehicle_unused_en(grid-export)=21632.31kWh , Total_supply=50639.7kWh , self-consump.rate=57.3 , Grid_cost=€  1487.07 , Total_selling_cost=€  606.05 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  80.89
Simulating VPP....


In [ ]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  12797.2 , Grid_used_en(grid-import)=34104.57kWh , Total_demand=63405.37kWh , autarky-rate=46.2 , RE-to-vehicle_unused_en(grid-export)=21307.37kWh , Total_supply=50608.16kWh , self-consump.rate=57.9 , Grid_cost=€  1484.33 , Total_selling_cost=€  614.38 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  80.89
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -6919.96 , Grid_used_en(grid-import)=1353.81kWh , Total_demand=53740.54kWh , autarky-rate=97.5 , RE-to-vehicle_unused_en(grid-export)=8273.77kWh , Total_supply=60660.5kWh , self-consump.rate=86.4 , Total_selling_cost=€  -257.17 , Grid_cost=€  57.0 
 EV_INFO: Av.EV_energy_leaving=kWh  72.43 , Std.EV_energy_leaving=kWh  22.99 , EV_departures =  1039 , EV_queue_left =  0
SCORE:  Cumulative_reward= 408260.4 - Step_rewars (load_t= 347099.48, EVs_ener

In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 01:00:00   0.000000   0.000000   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  92.689232  29.730255  75.459061  75.660072   
2022-06-06 05:00:00  92.689232  29.480255  77.255066  77.456078   
2022-06-06 05:15:00  93.866791  29.230255  78.432625  78.633636   
2022-06-06 05:30:00  95.083054  28.980255  79.648888  79.849899   
2022-06-06 05:45:00  96.270676  28.730255  80.836510  81.037521   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 01:00:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
...                                       ...           ...   
2022-06-06 04:45:00  [6675, 6676, 6674, 6677]  [0, 2, 1, 1]   
2022-06-06 05:00:00  [6675, 6676, 6674, 6677]  [1, 2, 1, 1]   
2022-06-06 05:15:00  [6675, 6676, 6674, 6677]  [1, 2, 1, 1]   
2022-06-06 05:30:00  [6675, 6676, 6674, 6677]  [1, 2, 1, 1]   
2022-06-06 05:45:00  [6675, 6676, 6674, 6677]  [1, 2, 1, 1]   

                                      mask_truth  ev_charged_pwr  \
time                                                               
2022-01-01 00:00:00  [False, False, False, True]        0.000000   
2022-01-01 00:15:00  [False, False, False, True]        0.000000   
2022-01-01 00:30:00  [False, False, False, True]        0.000000   
2022-01-01 00:45:00  [False, False, False, True]        0.000000   
2022-01-01 01:00:00  [False, False, False, True]        0.000000   
...                                          ...             ...   
2022-06-06 04:45:00    [True, False, True, True]       10.819076   
2022-06-06 05:00:00   [False, False, True, True]       14.368062   
2022-06-06 05:15:00   [False, False, True, True]       14.130688   
2022-06-06 05:30:00   [False, False, True, True]       14.595120   
2022-06-06 05:45:00   [False, False, True, True]       14.251480   

                     ev_discharged_pwr          load  load_reward  EV_reward  \
time                                                                           
2022-01-01 00:00:00                0.0 -3.899244e+00    -4.166426        0.0   
2022-01-01 00:15:00                0.0 -3.499856e+00    -4.404101        0.0   
2022-01-01 00:30:00                0.0 -3.642461e+00    -2.474349        0.0   
2022-01-01 00:45:00                0.0 -2.484610e+00    -3.768105        0.0   
2022-01-01 01:00:00                0.0 -3.260863e+00    -6.298285        0.0   
...                                ...           ...          ...        ...   
2022-06-06 04:45:00               -1.0  0.000000e+00    15.000000        0.0   
2022-06-06 05:00:00               -1.0  0.000000e+00    15.000000        0.0   
2022-06-06 05:15:00               -1.0 -1.776357e-15    15.000000        0.0   
2022-06-06 05:30:00               -1.0 -1.776357e-15    15.000000        0.0   
2022-06-06 05:45:00               -1.0  0.000000e+00    15.000000        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  -4.166426  
2022-01-01 00:15:00  -4.404101  
2022-01-01 00:30:00  -2.474349  
2022-01-01 00:45:00  -3.768105  
2022-01-01 01:00:00  -6.298285  
...                        ...  
2022-06-06 04:45:00  15.000000  
2022-06-06 05:00:00  15.000000  
2022-06-06 05:15:00  15.000000  
2022-06-06 05:30:00  15.000000  
2022-06-06 05:4

In [ ]:
env.plot_VPP_autarky()

In [ ]:
env.plot_VPP_results()


Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Training dataset VPP Simulation using the loaded trained model

In [ ]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 7302, Arrival time: 2022-01-01 07:45:00, Parking_time: 23.295663680087443, Leaving_time: 2022-01-02 07:02:44.389248, SOC: 0.7282439735809877, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 8344, Arrival time: 2022-12-31 22:45:00, Parking_time: 23.45613898593947, Leaving_time: 2023-01-01 22:12:22.100349, SOC: 0.4988600856422333, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , Grid_used_en(grid-import)=1556.25kWh , autarky-rate=90.5 , RE-to-vehicle_unused_en(grid-export)=-35673.95kWh , self-consump.rate=29.4 , Total_selling_cost=€  -1196.64 , Grid_cost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  8951.48 , Grid_used_en=kWh  32835.73 , RE-to-vehicle_unused_en=kWh  23884.25 , Total_selling_cost=€  444.38 , Grid_cost=€  1338.95 , Charging_events=  1043 
- Exp.VPP_goals: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  84.2


In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
#env.plot_VPP_input_data()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  7692.5 , Grid_used_en(grid-import)=31021.15kWh , Total_demand=58201.63kWh , autarky-rate=46.7 , RE-to-vehicle_unused_en(grid-export)=23328.65kWh , Total_supply=50509.13kWh , self-consump.rate=53.8 , Grid_cost=€  1300.81 , Total_selling_cost=€  436.77 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  84.2
Simulating VPP....


In [ ]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  8758.62 , Grid_used_en(grid-import)=32541.51kWh , Total_demand=59255.85kWh , autarky-rate=45.1 , RE-to-vehicle_unused_en(grid-export)=23782.89kWh , Total_supply=50497.24kWh , self-consump.rate=52.9 , Grid_cost=€  1365.81 , Total_selling_cost=€  493.07 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- VPP_goal_upper_limit: Grid_used_en=kWh 0, RE-to-vehicle_unused_en=kWh 0, Grid_cost=€ 0 , Av.EV_en_left=kWh  84.2
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -8842.0 , Grid_used_en(grid-import)=937.48kWh , Total_demand=51001.91kWh , autarky-rate=98.2 , RE-to-vehicle_unused_en(grid-export)=9779.48kWh , Total_supply=59843.92kWh , self-consump.rate=83.7 , Total_selling_cost=€  -304.64 , Grid_cost=€  39.28 
 EV_INFO: Av.EV_energy_leaving=kWh  74.43 , Std.EV_energy_leaving=kWh  22.6 , EV_departures =  1042 , EV_queue_left =  0
SCORE:  Cumulative_reward= 408846.06 - Step_rewars (load_t= 340713.36, EVs_energ

In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(14995)

0    1          2    3              EVs_id  \
time                                                                      
2022-01-01 00:00:00   0.000000  0.0   0.000000  0.0        [0, 0, 0, 0]   
2022-01-01 00:15:00   0.000000  0.0   0.000000  0.0        [0, 0, 0, 0]   
2022-01-01 00:30:00   0.000000  0.0   0.000000  0.0        [0, 0, 0, 0]   
2022-01-01 00:45:00   0.000000  0.0   0.000000  0.0        [0, 0, 0, 0]   
2022-01-01 01:00:00   0.000000  0.0   0.000000  0.0        [0, 0, 0, 0]   
...                        ...  ...        ...  ...                 ...   
2022-06-06 03:30:00  30.956566  0.0  99.989998  0.0  [9829, 0, 9828, 0]   
2022-06-06 03:45:00  30.956566  0.0  99.989998  0.0  [9829, 0, 9828, 0]   
2022-06-06 04:00:00  30.956566  0.0  99.989998  0.0  [9829, 0, 9828, 0]   
2022-06-06 04:15:00  30.956566  0.0  99.989998  0.0  [9829, 0, 9828, 0]   
2022-06-06 04:30:00  30.956566  0.0  99.989998  0.0  [9829, 0, 9828, 0]   

                          actions                   mask_truth  \
time                                                             
2022-01-01 00:00:00  [2, 1, 1, 0]  [False, False, False, True]   
2022-01-01 00:15:00  [2, 1, 1, 0]  [False, False, False, True]   
2022-01-01 00:30:00  [2, 1, 1, 0]  [False, False, False, True]   
2022-01-01 00:45:00  [2, 0, 1, 0]   [False, True, False, True]   
2022-01-01 01:00:00  [2, 0, 1, 0]   [False, True, False, True]   
...                           ...                          ...   
2022-06-06 03:30:00  [0, 0, 1, 2]  [False, True, False, False]   
2022-06-06 03:45:00  [0, 0, 1, 2]  [False, True, False, False]   
2022-06-06 04:00:00  [0, 0, 1, 2]  [False, True, False, False]   
2022-06-06 04:15:00  [0, 0, 1, 2]  [False, True, False, False]   
2022-06-06 04:30:00  [0, 0, 1, 2]  [False, True, False, False]   

                     ev_charged_pwr  ev_discharged_pwr      load  load_reward  \
time                                                                            
2022-01-01 00:00:00        0.000000                0.0 -2.831171    -3.698245   
2022-01-01 00:15:00        0.000000                0.0 -3.218947    -4.393172   
2022-01-01 00:30:00        0.000000                0.0 -3.635903    -5.277539   
2022-01-01 00:45:00        0.000000                0.0 -4.305292    -5.973174   
2022-01-01 01:00:00        0.000000                0.0 -5.070491    -5.474020   
...                             ...                ...       ...          ...   
2022-06-06 03:30:00        0.000009                0.0 -4.680760    -4.462009   
2022-06-06 03:45:00        0.000009                0.0 -3.677205    -7.349051   
2022-06-06 04:00:00        0.000009                0.0 -6.583956    -7.132009   
2022-06-06 04:15:00        0.000009                0.0 -6.345210    -7.262599   
2022-06-06 04:30:00        0.000009                0.0 -6.488859    -7.559882   

                     EV_reward   rewards  
time                                      
2022-01-01 00:00:00        0.0 -3.698245  
2022-01-01 00:15:00        0.0 -4.393172  
2022-01-01 00:30:00        0.0 -5.277539  
2022-01-01 00:45:00        0.0 -5.973174  
2022-01-01 01:00:00        0.0 -5.474020  
...                        ...       ...  
2022-06-06 03:30:00        0.0 -4.462009  
2022-06-06 03:45:00        0.0 -7.349051  
2022-06-06 04:00:00        0.0 -7.132009  
2022-06-06 04:15:00        0.0 -7.262599  
2022-06-06 04:30:00        0.0 -7.559882  

[14995 rows x 13 columns]

In [ ]:
env.plot_VPP_autarky()

In [ ]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_actions_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#env.close()